In [11]:
# Install necessary libraries
!pip install folium networkx geopandas osmnx

# Import libraries
import pandas as pd
import folium
from folium.plugins import HeatMap, MarkerCluster
import geopandas as gpd
import networkx as nx
import osmnx as ox
import unicodedata

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 323.6/323.6 kB 8.0 MB/s eta 0:00:00:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.4/99.4 kB 15.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.1/15.1 MB 84.8 MB/s eta 0:00:00:00:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.6/4.6 MB 22.9 MB/s eta 0:00:0000:0100:01m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 65.0 MB/s eta 0:00:00


In [12]:
# Part 1: Load and Clean Data for EV Charging Stations
# ========================================================
# Step 1.1: Load the EV charging station dataset
df = pd.read_csv('/Users/zactseng/Documents/ECE 1724 Bio/Project/EV_Charging_Stations_Placement_Optimization/Quebec_EV_charging_station.csv')

# Step 1.2: Normalize 'City' column by removing accents and converting to lowercase
df['City'] = df['City'].apply(lambda x: unicodedata.normalize('NFKD', x).encode('ASCII', 'ignore').decode('utf-8').lower())

# Step 1.3: Filter for rows where 'City' is 'montreal' and select specific columns
montreal_df = df[df['City'] == 'montreal']
montreal_df = montreal_df[['City', 'Latitude', 'Longitude', 'Price', 'Pricing']]

# Save the filtered dataset for later use
output_path = 'Montreal_EV_charging_stations.csv'
if not montreal_df.empty:
    montreal_df.to_csv(output_path, index=False)
else:
    print("No data found for 'Montreal' in the dataset after cleaning.")

In [13]:
# Part 2: Visualize EV Charging Stations with Price-Based Markers
# ========================================================
# Initialize a map centered on Montreal
montreal_map = folium.Map(location=[45.5017, -73.5673], zoom_start=12)

# Add markers for each charging station with color coding based on price
for index, row in montreal_df.iterrows():
    marker_color = "orange" if row['Price'] > 1 else "blue"
    folium.Marker(
        location=[row['Latitude'], row['Longitude']],
        popup=f"Price: {row['Price']}, Pricing: {row['Pricing']}",
        icon=folium.Icon(color=marker_color, icon="bolt", prefix="fa")
    ).add_to(montreal_map)

In [15]:
# Part 3: Buffer Analysis
# ========================================================
# Create a GeoDataFrame for spatial analysis
gdf = gpd.GeoDataFrame(
    montreal_df,
    geometry=gpd.points_from_xy(montreal_df['Longitude'], montreal_df['Latitude']),
    crs="EPSG:4326"
)

# Buffer Analysis: Create a 500-meter buffer around each charging station
gdf = gdf.to_crs(epsg=3395)  # Convert to a projected CRS for accurate buffering
gdf['buffer'] = gdf.geometry.buffer(500)

# Add buffer zones to the map
for _, row in gdf.iterrows():
    # Extract coordinates from the buffer's exterior
    buffer_coords = list(row['buffer'].exterior.coords)
    
    # Convert coordinates to (latitude, longitude) for folium
    buffer_locations = [(coord[1], coord[0]) for coord in buffer_coords]
    
    # Add buffer as a polygon to the map
    folium.Polygon(
        locations=buffer_locations,
        color="green",
        fill=True,
        fill_opacity=0.3
    ).add_to(montreal_map)

In [18]:
# Part 4: Network Analysis with Connectivity Check
# ========================================================
# Download road network for Montreal
montreal_graph = ox.graph_from_place("Montreal, Quebec, Canada", network_type="drive")

# Ensure the graph has edge lengths
montreal_graph = ox.distance.add_edge_lengths(montreal_graph)

# Retain only the largest connected component
montreal_graph = montreal_graph.subgraph(max(nx.strongly_connected_components(montreal_graph), key=len)).copy()

# Get nearest nodes for charging stations
nodes = []
for _, row in montreal_df.iterrows():
    try:
        nearest_node = ox.distance.nearest_nodes(
            montreal_graph, X=row['Longitude'], Y=row['Latitude']
        )
        nodes.append(nearest_node)
    except Exception as e:
        print(f"Error finding nearest node for charging station at ({row['Latitude']}, {row['Longitude']}): {e}")

# Define a sample residential location (Downtown Montreal)
sample_location = (45.5088, -73.554)

# Get the nearest node for the sample location
try:
    sample_node = ox.distance.nearest_nodes(
        montreal_graph, X=sample_location[1], Y=sample_location[0]
    )
except Exception as e:
    print(f"Error finding nearest node for sample location: {e}")
    sample_node = None

# Calculate shortest paths to each charging station
shortest_paths = {}
if sample_node is not None:
    for i, node in enumerate(nodes):
        try:
            if nx.has_path(montreal_graph, sample_node, node):
                path_length = nx.shortest_path_length(
                    montreal_graph, source=sample_node, target=node, weight="length"
                )
                shortest_paths[f"Station {i+1}"] = path_length
            else:
                print(f"Station {i+1}: Node {node} not reachable from sample location.")
        except Exception as e:
            print(f"Error calculating shortest path to Station {i+1}: {e}")

# Display shortest path results
if shortest_paths:
    print("Shortest path lengths (meters) from the sample location to each charging station:")
    for station, distance in shortest_paths.items():
        print(f"{station}: {distance:.2f} meters")
else:
    print("No shortest paths calculated.")

Shortest path lengths (meters) from the sample location to each charging station:
Station 1: 12002.76 meters
Station 2: 12002.76 meters
Station 3: 13662.77 meters
Station 4: 13662.77 meters
Station 5: 14288.15 meters
Station 6: 14288.15 meters
Station 7: 14003.94 meters
Station 8: 14003.94 meters
Station 9: 13186.74 meters
Station 10: 13186.74 meters
Station 11: 13186.74 meters
Station 12: 13186.74 meters
Station 13: 13806.40 meters
Station 14: 13806.40 meters
Station 15: 13806.40 meters
Station 16: 13806.40 meters
Station 17: 13806.40 meters
Station 18: 13806.40 meters
Station 19: 13806.40 meters
Station 20: 13806.40 meters
Station 21: 15271.78 meters
Station 22: 15271.78 meters
Station 23: 12945.72 meters
Station 24: 12945.72 meters
Station 25: 11900.70 meters
Station 26: 11900.70 meters
Station 27: 11900.70 meters
Station 28: 11900.70 meters
Station 29: 10992.14 meters
Station 30: 10992.14 meters
Station 31: 12400.96 meters
Station 32: 12400.96 meters
Station 33: 12367.18 meters
Sta

In [19]:
# Part 5: Add Heatmap for Charging Stations
# ========================================================
heat_data = [[row['Latitude'], row['Longitude']] for _, row in montreal_df.iterrows()]
HeatMap(heat_data).add_to(montreal_map)

# Display the map
montreal_map